In [1]:
# import library
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import csv

import pythainlp
import pythaispell
from gingerit.gingerit import GingerIt
from langdetect import detect
import nltk

from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from pythainlp.corpus import wordnet
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words

from pythainlp.corpus.common import thai_words
from pythainlp.tokenize import dict_trie
from pythainlp.tag.named_entity import ThaiNameTagger

In [2]:
# import data from csv
file_name = '0-4'
df = pd.read_csv('./Data/data{}.csv'.format(file_name))

In [3]:
df.head()

Unnamed: 0                                       category_0_0  \
0           0                          โทรศัพท์มือถือและแท็บเล็ต   
1           1                                        Smartphones   
2           2    Samsung Galaxy M30s (4/64GB) ( โทรศัพท์มือถือ )   
3           3  แบตอึดอยู่นาน สนุกได้ทั้งวัน กับความจุ 6000 mA...   
4           4  ระบบกล้องหลัง 3 ตัว ที่มีกล้องชัดสูงสุดถึง 48 ...   

                                        category_0_1  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2  โทรศัพท์มือถือ Samsung Galaxy A50s Ram4/64GB (...   
3                           GSM 850/900/1800/1900MHz   
4                      3G WCDMA 850/900/1900/2100MHz   

                                        category_0_2  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2               Samsung Galaxy A10s (RAM2GB/ROM32GB)   
3      สมาร์ทโฟน (โทรศัพท์มือถือพร้อมระบบปฏิบัติการ)   
4  จอแสดงผล TFT-LCD 24-bit (16 ล้านสี)- หน้าจอทรง...   

                                        category_0_3  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2  Samsung Galaxy Note 10 + (12/256 GB) ( โทรศัพท...   
3                                ขนาดหน้าจอ 6.8 นิ้ว   
4                                          Ram 12 GB   

                                        category_0_4  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2                           Samsung Galaxy A7 (2017)   
3  ระบบเซ็นเซอร์ (Sensor)\r\n- ระบบตรวจสอบลายนิ้ว...   
4  คุณสมบัติการกันน้ำ (Waterproof)\r\n- กันน้ำได้...   

                                        category_0_5  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2  Samsung Galaxy A9 (2018) 6 GB RAM 128 GB ROM 6...   
3  จอแสดงผล Super AMOLED 24-bit (16 ล้านสี)Fullvi...   
4  ระบบตรวจสอบลายนิ้วมือ (Fingerprint)ระบบจดจำใบห...   

                                        category_0_6  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2  Samsung A30S (RAM 4GB / ROM 64 GB) มือ 1 ประกั...   
3                             คุณสมบัติ Samsung A30S   
4           จอแสดงผล Super AMOLED 24-bit (16 ล้านสี)   

                                        category_0_7  \
0                          โทรศัพท์มือถือและแท็บเล็ต   
1                                        Smartphones   
2  (มือ1 ศูนย์ไทย) Samsung Galaxy Note 10 Plus No...   
3  Samsung Galaxy Note10 plus TH ประกันศูนย์ไทย 1...   
4                                      แบรนด์ ซัมซุง   

                                      category_0_8  ...  \
0                        โทรศัพท์มือถือและแท็บเล็ต  ...   
1                                      Smartphones  ...   
2  Samsung Galaxy A70 (8/128GB) ( โทรศัพท์มือถือ )  ...   
3                      Galaxy A70 (SM-A705FZBGTHL)  ...   
4                               สเปคเทพของเกมเมอร์  ...   

                                      category_4_245  \
0  ASUS Notebook(โน้ตบุ๊คเล่นเกมส์) ROG Zephyrus ...   
1  Asus Notebook ROG Strix G G531GT-AL017T i7-975...   
2  ASUS GAMING NOTEBOOK รุ่น A570ZD-DM133T\r\n฿ 1...   
3  Lenovo Y530 81FV01CPTA\r\n฿ 17,711.00\r\n฿ 19,...   
4  โน๊ตบุ๊ค ASUS Gaming FX504G Gaming Notebook i5...   

                                      category_4_246  \
0  Asus Gaming Notebook ROG STRIX GL504GV (ES036T...   
1  โน้ตบุ๊ค Gaming Notebook Acer Nitro5 AN515-43-...   
2  Asus TUF Gaming FX505DT AL106T /Ryzen5 3550H/1...   
3  โน๊ตบุ๊ค Acer Nitro AN515-54-76TH_Obsidian Bla...   
4  ASUS Notebook(โน้ตบุ๊คเล่นเกมส์)TUF FX505GE-BQ...   

                                      category_4_247  \
0                             คอมพิวเตอร์ & แล็ปท็อป   
1                                           แล็ปท็อป   
2                            แล็ปท็อปส

In [4]:
# Process data such as drop NaN and drop column that do not use
# Drop column and row that equal to NaN
df = df.dropna(axis=1, how='all')
df = df.dropna(axis=0, how='all')

# Fill NaN with "-"
df = df.fillna('-')

# Drop a column that is index
df = df.drop(columns=['Unnamed: 0'])

In [6]:
df.describe()

category_0_0 category_0_1 category_0_2 category_0_3 category_0_4  \
count           108          108          108          108          108   
unique           14           33           23           16           47   
top               -            -            -            -            -   
freq             95           76           86           93           62   

       category_0_5 category_0_6 category_0_7 category_0_8 category_0_9  ...  \
count           108          108          108          108          108  ...   
unique           16           29           13           14           19  ...   
top               -            -            -            -            -  ...   
freq             93           80           96           95           90  ...   

       category_4_245 category_4_246 category_4_247 category_4_248  \
count             108            108            108            108   
unique             13             13              5             13   
top                 -              -              -              -   
freq               96             96            104             96   

       category_4_249 category_4_250 category_4_251 category_4_252  \
count             108            108            108            108   
unique              5              5              5              5   
top                 -              -              -              -   
freq              104            104            104            104   

       category_4_253 category_4_254  
count             108            108  
unique              5              5  
top                 -              -  
freq              104            104  

[4 rows x 1099 columns]

# Process text

In [7]:
import re
import string

from pythainlp.tokenize import Tokenizer

# word correction for EN
#parser = GingerIt()

# download stopwords of TH and EN
nltk.download('words')
th_stop = tuple(thai_stopwords())
en_stop = tuple(get_stop_words('en'))
p_stemmer = PorterStemmer()

# path of custom dictionary for word tokenize
PATH_TO_CUSTOM_DICT = './Data/custom_dict.txt'

# clean the text
def clean_text(msg): 

    #msg = re.sub(r"SKU\s+\d+\_TH\-\d+"," ",str(msg))
    msg = re.sub(r"ƒ","f",str(msg))
    msg = re.sub(r"[^A-Za-z0-9ก-๙\.\,\s\฿\%\:\-\_]"," ", str(msg))
    #msg = re.sub(r"[A-Za-z]{30,}"," ",str(msg))
    
    # Delete punctuation
   # str_punc = string.punctuation.replace(".","")
   # for c in str_punc:
    #    msg = re.sub(r'\{}'.format(c),'',str(msg))
    
    # ลบ separator เช่น \n \t
    msg = ' '.join(msg.split())
    
    return msg

# split to words from text
def split_word(text):
    
    # Split text to words
    _tokenizer = Tokenizer(custom_dict=PATH_TO_CUSTOM_DICT, engine='newmm')
    words = _tokenizer.word_tokenize(text)

    # Remove stop words in TH and EN
    words = [i for i in words if not i in th_stop and not i in en_stop]
    
    # รากศัพท์
    # EN
    #words = [p_stemmer.stem(i) for i in words]
    
    # TH
    #tokens_temp=[]
    #for i in words:
    #    w_syn = wordnet.synsets(i)
    #    if (len(w_syn)>0) and (len(w_syn[0].lemma_names('tha'))>0) and not (w_syn[0].lemma_names('tha')[0].isdigit()):
    #        tokens_temp.append(w_syn[0].lemma_names('tha')[0])
    #    else:
     #       tokens_temp.append(i)
    
    #words = tokens_temp
    
    # Delete whitespace
    words = [i for i in words if not ' ' in i]

    return words

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\super\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


In [8]:
# Cleaning text with clean_text function and keep in dict
data_clean = {}
for key,value in df.iteritems():
    tmp = [clean_text(txt) for txt in value if not txt == '-']
    data_clean[key] = tmp 
    

In [9]:
data_clean

{'category_0_0': ['โทรศัพท์มือถือและแท็บเล็ต',
  'Smartphones',
  'Samsung Galaxy M30s 4 64GB โทรศัพท์มือถือ',
  'แบตอึดอยู่นาน สนุกได้ทั้งวัน กับความจุ 6000 mAh และสามารถชาร์จแบตเร็ว ด้วย Fast Charging',
  'ระบบกล้องหลัง 3 ตัว ที่มีกล้องชัดสูงสุดถึง 48 MP มาพร้อมกับเลนส์มุมกว้างพิเศษ Ultra Wide',
  'ใช้ Exynos 9611 สเป็กแรงขึ้นเล่นเกมส์ได้ไม่มีสะดุด กับ RAM 4 GB ROM 64 GB',
  'หน้าจอแสดงผล Super AMOLED Infinity-U ขนาด 6.4 นิ้ว',
  'แบรนด์ ซัมซุง',
  'SKU 480942616_TH-870640886',
  'ประเภทของการรับประกัน มีการรับประกัน',
  'Model Galaxy M30s 4 64GB',
  'ระยะเวลาการรับประกัน 1 ปี',
  '793'],
 'category_0_1': ['โทรศัพท์มือถือและแท็บเล็ต',
  'Smartphones',
  'โทรศัพท์มือถือ Samsung Galaxy A50s Ram4 64GB รับประกันศูนย์ By Jaymart',
  'GSM 850 900 1800 1900MHz',
  '3G WCDMA 850 900 1900 2100MHz',
  '4G FDD LTE B1 2100 , B3 1800 , B5 850 , B7 2600 , B8 900 , B20 800 , B28 700',
  '4G TDD LTE B38 2600 , B40 2300 , B41 2500',
  'รองรับ 2 ซิม Nano-SIM',
  'หน่วยประมวลผล Exynos 9610 Quad 2.3 GHz

In [10]:
# Split the cleaned text to words by using split_word function ,then keep in dict
token = {}
for key,value in data_clean.items():
    tmp = [split_word(txt) for txt in value]
    token[key] = tmp


In [11]:
token

{'category_0_0': [['โทรศัพท์มือถือและแท็บเล็ต'],
  ['Smartphones'],
  ['Samsung', 'Galaxy', 'M', '30', 's', '4', '64', 'GB', 'โทรศัพท์มือถือ'],
  ['แบต',
   'อึดอยู่นาน',
   'สนุกได้ทั้งวัน',
   'กับความจุ',
   '6000',
   'mAh',
   'และสามารถชาร์จ',
   'แบต',
   'Fast',
   'Charging'],
  ['ระบบ',
   'กล้องหลัง',
   '3',
   'ตัว',
   'ที่มีกล้องชัดสูงสุดถึง',
   '48',
   'MP',
   'มาพร้อมกับเลนส์มุมกว้างพิเศษ',
   'Ultra',
   'W',
   'ide'],
  ['Exynos',
   '9611',
   'สเป็กแรงขึ้นเล่นเกมส์ได้ไม่มีสะดุด',
   'RAM',
   '4',
   'GB',
   'ROM',
   '64',
   'GB'],
  ['หน้าจอแสดงผล', 'Super', 'AMOLED', 'Infinity-U', 'ขนาด', '6.4', 'นิ้ว'],
  ['แบรนด์', 'ซัมซุง'],
  ['SKU', '480942616', '_', 'TH-', '870640886'],
  ['ประเภทของการรับประกัน', 'มีการรับประกัน'],
  ['Model', 'Galaxy', 'M', '30', 's', '4', '64', 'GB'],
  ['ระยะเวลาการรับประกัน', '1', 'ปี'],
  ['793']],
 'category_0_1': [['โทรศัพท์มือถือและแท็บเล็ต'],
  ['Smartphones'],
  ['โทรศัพท์มือถือ',
   'Samsung',
   'Galaxy',
   'A',
   '50'

In [55]:
#series = { key: pd.Series(val) for key, val in token.items() }
#series

{'category_536_0': 0                                       [ไฟ, ของตกแต่ง]
 1                                              [หลอดไฟ]
 2                                       [หลอดแบล็คไลท์]
 3     [ไฟ, LED, จากพลังงานโซล่าเซลล์โคมไฟแขวนหลอดไฟ,...
 4                                      [วัสดุ, เอบีเอส]
 5                                 [แหล่งกำเนิดแสง, LED]
 6                                       [สินค้าสี, ขาว]
 7                                          [แสงสี, ขาว]
 8        [แหล่งจ่ายไฟ, Built, แบตเตอรี่, แบบชาร์จไฟได้]
 9                                  [เกรดกันน้ำ, IP, 44]
 10                                  [แบรนด์, easygobuy]
 11                     [SKU, 555626537, TH, 1016410778]
 12              [ประเภทของการรับประกัน, ไม่มีการประกัน]
 13    [รุ่น, easygoingbuy, 3, RB, 2, AW, 2, NC, 6, Y...
 dtype: object,
 'category_536_1': 0                                       [ไฟ, ของตกแต่ง]
 1                                              [หลอดไฟ]
 2                                  

In [61]:
for i,v in series.items():
    series[i] = v.apply(pd.Series).stack()

#print(series)

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [63]:
# Transform dict to dataframe
text_processed = pd.DataFrame.from_dict(series, orient='index')

In [64]:
# Transpose dataframe and save
text_processed.transpose().to_csv('./Data/536-585.csv')
print(text_processed.transpose())

        category_536_0                               category_536_1  \
0  0  0             ไฟ                                           ไฟ   
   1  0      ของตกแต่ง                                    ของตกแต่ง   
1  0  0         หลอดไฟ                                       หลอดไฟ   
2  0  0  หลอดแบล็คไลท์                                หลอดแบล็คไลท์   
3  0  0             ไฟ  พับแอลอีดีมุมกว้างรูปฟุตบอลเคสระบายความร้อน   
...                ...                                          ...   
19 45 0            NaN                                          NaN   
   46 0            NaN                                          NaN   
   47 0            NaN                                          NaN   
   48 0            NaN                                          NaN   
   49 0            NaN                                          NaN   

                           category_536_2 category_536_4     category_536_5  \
0  0  0                                ไฟ             ไฟ            

# convert list of tuples to dataframe

list_df = []
for i,l in enumerate(pos_token):
    df = pd.DataFrame(l, columns=['word', 'pos'])
    df.insert(0,'idx',i)
    list_df.append(df)

data_for_excel = pd.concat(list_df,ignore_index=True)

data_for_excel

data_for_excel.to_excel('./Data/Sheet0_token.xlsx',engine='xlsxwriter')